In [2]:
import geopandas as gpd
import libpysal as lp
import pandas as pd
import os
import pyarrow as pa
import pyarrow.parquet as pq
import numpy as np


In [49]:
# map_2024_path = "../../housing-data/cbsgebiedsindelingen2016-2025/cbsgebiedsindelingen2024.gpkg"
map_2023_path = "../../housing-data/cbsgebiedsindelingen2016-2025/cbsgebiedsindelingen2023.gpkg"
# map_2022_path = "../../housing-data/cbsgebiedsindelingen2016-2025/cbsgebiedsindelingen2022.gpkg"
# map_2021_path = "../../housing-data/cbsgebiedsindelingen2016-2025/cbsgebiedsindelingen2021.gpkg"
# map_2020_path = "../../housing-data/cbsgebiedsindelingen2016-2025/cbsgebiedsindelingen2020.gpkg"
# map_2019_path = "../../housing-data/cbsgebiedsindelingen2016-2025/cbsgebiedsindelingen2019.gpkg"
# map_2018_path = "../../housing-data/cbsgebiedsindelingen2016-2025/cbsgebiedsindelingen2018.gpkg"
# map_2017_path = "../../housing-data/cbsgebiedsindelingen2016-2025/cbsgebiedsindelingen2017.gpkg"
# map_2016_path = "../../housing-data/cbsgebiedsindelingen2016-2025/cbsgebiedsindelingen2016.gpkg"
# map_2015_path = "../../housing-data/cbsgebiedsindelingen2016-2025/cbsgebiedsindelingen2015.gpkg"
# map_2014_path = "../../housing-data/cbsgebiedsindelingen2016-2025/cbsgebiedsindelingen2014.gpkg"

# district_info_path = "../../housing-data/district_info.csv"

In [62]:
def read_file(file_path, layer="gemeente_gegeneraliseerd"):
    gdf = gpd.read_file(file_path, layer=layer)
    #gdf = gdf[gdf['indelingswijziging_wijken_en_buurten'] > 0] -- Wel of niet???
    gdf_neighbors = lp.weights.Queen.from_dataframe(gdf, use_index=False)
    gdf_neighbors.to_sparse()
    codes = gdf.iloc[:, :1].to_numpy().flatten()
    adj_df = pd.DataFrame.sparse.from_spmatrix(
        gdf_neighbors.to_sparse(), index=codes, columns=codes
    )
    return adj_df, gdf

In [63]:
adj_df_2023, gdf_2023 = read_file(map_2023_path)
# _,gdf_2024 = read_file(map_2024_path)
# _,gdf_2022 = read_file(map_2022_path)
# _,gdf_2021 = read_file(map_2021_path)
# _,gdf_2020 = read_file(map_2020_path)
# _,gdf_2019 = read_file(map_2019_path)
# _,gdf_2018 = read_file(map_2018_path)
# _,gdf_2017 = read_file(map_2017_path)
# _,gdf_2016 = read_file(map_2016_path)
# _,gdf_2015 = read_file(map_2015_path)
# _,gdf_2014 = read_file(map_2014_path)


c:\Users\AratrikaD\gnns-for-property-valuation\.venv\lib\site-packages\libpysal\weights\contiguity.py:347: UserWarning: The weights matrix is not fully connected: 
 There are 6 disconnected components.
 There are 3 islands with ids: 6, 12, 132.
  W.__init__(self, neighbors, ids=ids, **kw)


In [64]:
gdf_2023

statcode  jrstatcode        statnaam   rubriek   id  \
0     GM0014  2023GM0014       Groningen  gemeente    1   
1     GM0034  2023GM0034          Almere  gemeente    2   
2     GM0037  2023GM0037     Stadskanaal  gemeente    3   
3     GM0047  2023GM0047         Veendam  gemeente    4   
4     GM0050  2023GM0050        Zeewolde  gemeente    5   
..       ...         ...             ...       ...  ...   
337   GM1979  2023GM1979       Eemsdelta  gemeente  338   
338   GM1980  2023GM1980   Dijk en Waard  gemeente  339   
339   GM1982  2023GM1982  Land van Cuijk  gemeente  340   
340   GM1991  2023GM1991       Maashorst  gemeente  341   
341   GM1992  2023GM1992  Voorne aan Zee  gemeente  342   

                                              geometry  
0    MULTIPOLYGON (((245194.691 592594.007, 245344....  
1    MULTIPOLYGON (((146891.056 493291.709, 147422....  
2    MULTIPOLYGON (((263763.866 566430.392, 263988....  
3    MULTIPOLYGON (((256231.909 572319.213, 258595....  
4    MULTIPOLYGON (((170596.293 486786.456, 170560....  
..                                                 ...  
337  MULTIPOLYGON (((254210.03 603122.465, 254836.2...  
338  MULTIPOLYGON (((114834.321 526066.026, 114919....  
339  MULTIPOLYGON (((181384.076 418252.229, 182100 ...  
340  MULTIPOLYGON (((176672.671 418565.125, 176593....  
341  MULTIPOLYGON (((74563.33 427012.72, 74542.72 4...  

[342 rows x 6 columns]

In [48]:
adj_df_2023.to_csv("../../housing-data/buurt_adj_2023.csv")

In [ ]:
def get_overlap_percentage(gdf_2023, gdf_old):
    """
    Calculates the overlap wts between old area and new area for each neighborhood
    """
    gdf_old = gdf_old.to_crs(gdf_2023.crs)

    intersections = gpd.overlay(gdf_old, gdf_2023,how="intersection",keep_geom_type=False)

    intersections['overlap_area'] = intersections.area

    gdf_old['area'] = gdf_old.area

    intersections = intersections.merge(
        gdf_old[["statcode", "area"]],
        left_on="statcode_1",
        right_on="statcode"
    )
    intersections["overlap_percentage"] = intersections["overlap_area"]/ intersections["area"]

    overlap_table = intersections[intersections['overlap_percentage']>0.01][['statcode_1', 'statcode_2','overlap_percentage']]
    overlap_table.columns= ["old_buurtcode","new_buurtcode","overlap_percentage"]
    overlap_table = overlap_table.sort_values(by=['new_buurtcode','overlap_percentage'])
    overlap_table = overlap_table.reset_index(drop=True)
    print(overlap_table.head(20))
    return overlap_table


In [ ]:
# def get_past_features(overlap_table, old_features, new_features, year):
#     for name, group in overlap_table.groupby('new_buurtcode'):
#         if len(group) == 1:
#             print(group)
#             features = old_features[old_features["BUURTCODE"] == group.iloc[0]["old_buurtcode"]].drop(["BUURTCODE"], axis=1).to_numpy().flatten()
#         else:
#             print(group)
#             features = np.array([0 for _ in range(len(new_features.columns) -2)])
#             for index, row in group.iterrows():
#                 # print(old_features[old_features["BUURTCODE"] == row["old_buurtcode"]].drop(["BUURTCODE"],axis=1))
#                 old_f = old_features[old_features["BUURTCODE"] == row["old_buurtcode"]].drop(["BUURTCODE"],axis=1).to_numpy().flatten()
#                 features = features + row["overlap_percentage"]*old_f



#         new_features_entry = [name,year]+features.tolist()
#         print(new_features_entry)
        
#         new_features.loc[len(new_features)] = new_features_entry
#         # print(new_features)

#     return new_features





## Cleaning District Info File

In [8]:
district_info = pd.read_csv(district_info_path)
district_info

BUURTCODE PEILDATUM  LEEFBAAROMETER     GROEN        EC       NO2  \
0       BU00030007  1/1/2018        4.195031  0.028880  0.000294  0.009311   
1       BU00030007  1/1/2019        4.195124  0.028869  0.000294  0.009312   
2       BU00030007  1/1/2020        4.169609  0.028895  0.000224  0.007272   
3       BU00030008  1/1/2014        4.251458  0.043239  0.000285  0.009420   
4       BU00030008  1/1/2015        4.251458  0.043239  0.000285  0.009420   
...            ...       ...             ...       ...       ...       ...   
147600  BU19450201  1/1/2024        4.227346  0.053809  0.000244  0.010508   
147601  BU19450300  1/1/2024        4.147552  0.034181  0.000237  0.010177   
147602  BU19450301  1/1/2024        4.213128  0.046378  0.000238  0.010148   
147603  BU19450400  1/1/2024        4.276418  0.046571  0.000253  0.011890   
147604  BU19450500  1/1/2024        4.160638  0.036006  0.000268  0.011427   

           PM2_5      PM10  GELUIDSHINDERTOTAAL  AFSTANDTOTHUISARTSENPRAKTIJK  \
0       0.007416  0.013866             0.307536                           2.0   
1       0.007414  0.013863             0.307441                           2.1   
2       0.006450  0.012967             0.307923                           2.1   
3       0.007372  0.013800             0.319748                           3.0   
4       0.007372  0.013800             0.319748                           3.0   
...          ...       ...                  ...                           ...   
147600  0.008375  0.015093             0.282222                           1.3   
147601  0.008276  0.014974             0.271579                           2.5   
147602  0.008287  0.014996             0.261597                           2.7   
147603  0.008367  0.015066             0.298843                           1.9   
147604  0.008936  0.015956             0.320351                           0.6   

        ...  MATEVANSTEDELIJKHEID  OMGEVINGSADRESSENDICHTHEID  \
0       ...                     5                         348   
1       ...                     5                         359   
2       ...                     5                         362   
3       ...                     5                          71   
4       ...                     5                          72   
...     ...                   ...                         ...   
147600  ...                     5                         291   
147601  ...                     5                         147   
147602  ...                     5                         205   
147603  ...                     5                          75   
147604  ...                     3                        1225   

        GEMIDDELDEWOZWAARDEVANWONINGEN  TOTAALDIEFSTALUITWONINGSCHUURED  \
0                                298.0                              0.0   
1                                298.0                              0.0   
2                                298.0                              0.0   
3                                285.0                             10.0   
4                                285.0                             10.0   
...                                ...                              ...   
147600                           522.0                              4.0   
147601                           349.0                             11.0   
147602                           486.0                              6.0   
147603                           379.0                              2.0   
147604                           310.0                              0.0   

        GEWELDSENSEKSUELEMISDRIJVEN  VERNIELINGMISDRIJFTEGENOPENBAREORDE  \
0                               3.0                                  3.0   
1                               3.0                                  3.0   
2                               3.0                                  3.0   
3                               0.0                                 20.0   
4                               0.0  

In [9]:
district_info["PEILDATUM"] = pd.to_datetime(district_info["PEILDATUM"])
district_info["PEILDATUM"] = district_info["PEILDATUM"].dt.year
district_info["PEILDATUM"]

0         2018
1         2019
2         2020
3         2014
4         2015
          ... 
147600    2024
147601    2024
147602    2024
147603    2024
147604    2024
Name: PEILDATUM, Length: 147605, dtype: int32

In [10]:
coutns = district_info.isna().sum()
drop_list = coutns[coutns >10000]
drop_list = drop_list.index.values
drop_list

array(['AFSTANDTOTCONSULTATIEBUREAU', 'AFSTANDTOTFYSIOTHERAPEUT',
       'FYSIOTHERAPEUTBINNEN1KM', 'FYSIOTHERAPEUTBINNEN3KM',
       'FYSIOTHERAPEUTBINNEN5KM', 'AFSTANDTOTOPENBAARGROENTOTAAL',
       'AFSTANDTOTPARKOFPLANTSOEN', 'AFSTANDTOTDAGRECREATIEFTERREIN',
       'AFSTANDTOTBOS', 'AFSTANDTOTOPENNATTERREINTOTAAL',
       'AFSTANDTOTOPENDROOGNATTERREIN',
       'AFSTANDTOTOPENNATNATUURLIJKTERREIN',
       'AFSTANDTOTSEMIOPENBAARGROENTOTAAL', 'AFSTANDTOTSPORTTERREIN',
       'AFSTANDTOTVOLKSTUIN', 'AFSTANDTOTVERBLIJFSRECREATIEFTERREIN',
       'AFSTANDTOTBEGRAAFPLAATS', 'AFSTANDTOTRECREATIEFBINNENWATER',
       'PERCENTAGEWONINGENMETSTADSVERWARMING', 'OPLEIDINGSNIVEAULAAG',
       'OPLEIDINGSNIVEAUMIDDELBAAR', 'OPLEIDINGSNIVEAUHOOG',
       'GEMIDDELDEWOZWAARDEVANWONINGEN',
       'TOTAALDIEFSTALUITWONINGSCHUURED', 'GEWELDSENSEKSUELEMISDRIJVEN',
       'VERNIELINGMISDRIJFTEGENOPENBAREORDE', 'OQOVERHEIDONDERWIJSENZORG'],
      dtype=object)

In [11]:
district_info.drop(drop_list, axis =1,inplace=True)

In [12]:
district_info.fillna(-999)

BUURTCODE  PEILDATUM  LEEFBAAROMETER     GROEN        EC       NO2  \
0       BU00030007       2018        4.195031  0.028880  0.000294  0.009311   
1       BU00030007       2019        4.195124  0.028869  0.000294  0.009312   
2       BU00030007       2020        4.169609  0.028895  0.000224  0.007272   
3       BU00030008       2014        4.251458  0.043239  0.000285  0.009420   
4       BU00030008       2015        4.251458  0.043239  0.000285  0.009420   
...            ...        ...             ...       ...       ...       ...   
147600  BU19450201       2024        4.227346  0.053809  0.000244  0.010508   
147601  BU19450300       2024        4.147552  0.034181  0.000237  0.010177   
147602  BU19450301       2024        4.213128  0.046378  0.000238  0.010148   
147603  BU19450400       2024        4.276418  0.046571  0.000253  0.011890   
147604  BU19450500       2024        4.160638  0.036006  0.000268  0.011427   

           PM2_5      PM10  GELUIDSHINDERTOTAAL  AFSTANDTOTHUISARTSENPRAKTIJK  \
0       0.007416  0.013866             0.307536                           2.0   
1       0.007414  0.013863             0.307441                           2.1   
2       0.006450  0.012967             0.307923                           2.1   
3       0.007372  0.013800             0.319748                           3.0   
4       0.007372  0.013800             0.319748                           3.0   
...          ...       ...                  ...                           ...   
147600  0.008375  0.015093             0.282222                           1.3   
147601  0.008276  0.014974             0.271579                           2.5   
147602  0.008287  0.014996             0.261597                           2.7   
147603  0.008367  0.015066             0.298843                           1.9   
147604  0.008936  0.015956             0.320351                           0.6   

        ...  OPPERVLAKTETOTAAL  OPPERVLAKTELAND  OPPERVLAKTEWATER  \
0       ...                559              540                18   
1       ...                559              540                18   
2       ...                559              540                18   
3       ...                582              554                28   
4       ...                582              554                28   
...     ...                ...              ...               ...   
147600  ...                495              495                 0   
147601  ...                 21               21                 0   
147602  ...                654              654                 0   
147603  ...                366              315                51   
147604  ...                 54               54                 0   

        MEESTVOORKOMENDEPOSTCODE  DEKKINGSPERCENTAGE  MATEVANSTEDELIJKHEID  \
0                         9903.0                 4.0                     5   
1                         9903.0                 4.0                     5   
2                         9903.0                 4.0                     5   
3                         9902.0                 1.0                     5   
4                         9902.0                 1.0                     5   
...                          ...                 ...                   ...   
147600                    6562.0                 1.0                     5   
147601                    6562.0                 1.0                     5   
147602                    6562.0                 2.0                     5   
147603                    6577.0                 1.0                     5   
147604                    6562.0                 1.0                     3   

        OMGEVINGSADRESSENDICHTHEID  VLIEGTUIG  TREIN  GELUIDSHINDERINDUSTRIE  
0                              348        0.5    0.1                     1.3  
1                              359        0.5    0.1                     1.3  
2                              362        0.5    0.1                     1.3  
3    

In [13]:
district_info.rename(columns={"PEILDATUM": "DATUM"}, inplace=True)

## Calculating new neighborhood code feature values

In [ ]:
import pandas as pd
import numpy as np
from tqdm import tqdm

def process_year(overlap_table, district_info, feature_cols, year, nan_value=-999):
    """
    Process features for one year based on the overlap table
    TODO: Check the logic
    """
    new_buurts = adj_df_2023.columns.values
    print(set(overlap_table['new_buurtcode'].unique()).difference(set(new_buurts)))
    new_features = ['BUURTCODE', 'YEAR'] + feature_cols
    
    result = pd.DataFrame(columns=new_features)
    result['BUURTCODE'] = new_buurts
    result['YEAR'] = year
  
    # Initialize features with nan_value
    for feature in feature_cols:
        result[feature] = nan_value

    # Filter feature dataframe for that year
    year_info = district_info[district_info['DATUM'] == year]
    new_buurts = overlap_table['new_buurtcode'].unique()
    for new_code in tqdm(new_buurts, desc=f"Processing {year}"):
        overlaps = overlap_table[overlap_table['new_buurtcode'] == new_code]
        
        valid_weights = []
        feature_values = {f: [] for f in feature_cols}

        for _, row in overlaps.iterrows():
            old_code = row['old_buurtcode']
            weight = row['overlap_percentage'] 

            old_row = year_info[year_info['BUURTCODE'] == old_code]

            if old_row.empty:
                continue

            valid = False
            for feature in feature_cols:
                value = old_row[feature].values[0] if len(old_row) > 0 else nan_value
                if value != nan_value:
                    feature_values[feature].append(weight * value)
                    valid = True

            if valid:
                valid_weights.append(weight)

        if len(valid_weights) > 0:
            valid_weights = np.array(valid_weights)
            valid_weights /= valid_weights.sum()  # Renormalize weights

            for feature in feature_cols:
                if len(feature_values[feature]) > 0:
                    result.loc[result['BUURTCODE'] == new_code, feature] = np.sum(valid_weights * np.array(feature_values[feature]))
    result.to_csv(f"../../housing-data/neighborhood_features/year-{year}.csv", index=False)
    return result


def create_final_table(overlap_tables, district_info, feature_cols, nan_value=-999):
    """
    Create the full spatio-temporal table from 2014 to 2023
    """
    all_years = []

    for year, overlap_table in overlap_tables.items():
        year_table = process_year(overlap_table, district_info, feature_cols, year, nan_value)



In [19]:
overlap_table_2024 = get_overlap_percentage(gdf_2023, gdf_2024)
overlap_table_2023 = get_overlap_percentage(gdf_2023, gdf_2023)
overlap_table_2022 = get_overlap_percentage(gdf_2023, gdf_2022)
overlap_table_2021 = get_overlap_percentage(gdf_2023, gdf_2021)
overlap_table_2020 = get_overlap_percentage(gdf_2023, gdf_2020)
overlap_table_2019 = get_overlap_percentage(gdf_2023, gdf_2019)
overlap_table_2018 = get_overlap_percentage(gdf_2023, gdf_2018)
overlap_table_2017 = get_overlap_percentage(gdf_2023, gdf_2017)
overlap_table_2016 = get_overlap_percentage(gdf_2023, gdf_2016)
overlap_table_2015 = get_overlap_percentage(gdf_2023, gdf_2015)
overlap_table_2014 = get_overlap_percentage(gdf_2023, gdf_2014)

   old_buurtcode new_buurtcode  overlap_percentage
0     BU00140000    BU00140000                 1.0
1     BU00140001    BU00140001                 1.0
2     BU00140002    BU00140002                 1.0
3     BU00140003    BU00140003                 1.0
4     BU00140004    BU00140004                 1.0
5     BU00140005    BU00140005                 1.0
6     BU00140007    BU00140007                 1.0
7     BU00140008    BU00140008                 1.0
8     BU00140100    BU00140100                 1.0
9     BU00140101    BU00140101                 1.0
10    BU00140102    BU00140102                 1.0
11    BU00140103    BU00140103                 1.0
12    BU00140104    BU00140104                 1.0
13    BU00140105    BU00140105                 1.0
14    BU00140106    BU00140106                 1.0
15    BU00140107    BU00140107                 1.0
16    BU00140108    BU00140108                 1.0
17    BU00140109    BU00140109                 1.0
18    BU00140110    BU00140110 

In [20]:

overlap_tables = {
    # 2014: overlap_table_2014,
    # 2015: overlap_table_2015,
    # 2016: overlap_table_2016,
    # 2017: overlap_table_2017,
    # 2018: overlap_table_2018,
    # 2019: overlap_table_2019,
    # 2020: overlap_table_2020,
    # 2021: overlap_table_2021,
    2022: overlap_table_2022,
    2023: overlap_table_2023,
    2024: overlap_table_2024
}


feature_cols = district_info.drop(["BUURTCODE", "DATUM"],axis=1).columns.values.tolist()

nan_value = -999

final_table = create_final_table(overlap_tables, district_info, feature_cols, nan_value)
final_table
# # Save the result
# final_table.to_csv('spatio_temporal_features.csv', index=False)
# print(" Final table created!")

set()


Processing 2022:   0%|          | 0/14418 [00:00<?, ?it/s]C:\Users\AratrikaD\AppData\Local\Temp\ipykernel_16088\69687545.py:55: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '4.168289990087371' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  result.loc[result['BUURTCODE'] == new_code, feature] = np.sum(valid_weights * np.array(feature_values[feature]))
C:\Users\AratrikaD\AppData\Local\Temp\ipykernel_16088\69687545.py:55: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '0.005793934110305606' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  result.loc[result['BUURTCODE'] == new_code, feature] = np.sum(valid_weights * np.array(feature_values[feature]))
C:\Users\AratrikaD\AppData\Local\Temp\ipykernel_16088\69687545.py:55: FutureWarning: Setting an ite

set()


Processing 2023:   0%|          | 0/14421 [00:00<?, ?it/s]C:\Users\AratrikaD\AppData\Local\Temp\ipykernel_16088\69687545.py:55: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '4.349847838662413' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  result.loc[result['BUURTCODE'] == new_code, feature] = np.sum(valid_weights * np.array(feature_values[feature]))
C:\Users\AratrikaD\AppData\Local\Temp\ipykernel_16088\69687545.py:55: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '0.0060345' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  result.loc[result['BUURTCODE'] == new_code, feature] = np.sum(valid_weights * np.array(feature_values[feature]))
C:\Users\AratrikaD\AppData\Local\Temp\ipykernel_16088\69687545.py:55: FutureWarning: Setting an item of incomp

set()


Processing 2024:   0%|          | 0/14421 [00:00<?, ?it/s]C:\Users\AratrikaD\AppData\Local\Temp\ipykernel_16088\69687545.py:55: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '4.34984783863563' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  result.loc[result['BUURTCODE'] == new_code, feature] = np.sum(valid_weights * np.array(feature_values[feature]))
C:\Users\AratrikaD\AppData\Local\Temp\ipykernel_16088\69687545.py:55: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '0.006034499999962844' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  result.loc[result['BUURTCODE'] == new_code, feature] = np.sum(valid_weights * np.array(feature_values[feature]))
C:\Users\AratrikaD\AppData\Local\Temp\ipykernel_16088\69687545.py:55: FutureWarning: Setting an item

## Combining feature files for all years

In [1]:


def create_final_table():
    """
    Create the full spatio-temporal table from 2014 to 2023
    """
    all_years = []

    years = [2014, 2015, 2016, 2017, 2018, 2019, 2020, 2021, 2022, 2023, 2024]
    for year in years:
        year_table = pd.read_csv(f"../../housing-data/neighborhood_features/year-{year}.csv")
        print(len(year_table))
        all_years.append(year_table)

    combined = pd.concat(all_years, ignore_index=True)

    return combined
        

In [3]:

all_features  = create_final_table()
all_features

14421
14421
14421
14421
14421
14421
14421
14421
14421
14421
14421


BUURTCODE  YEAR  LEEFBAAROMETER     GROEN        EC       NO2  \
0       BU00340101  2014        0.422447  0.002708  0.000055  0.001401   
1       BU00340102  2014        3.028834  0.018978  0.000391  0.010034   
2       BU00340201  2014        0.984693  0.009806  0.000132  0.003380   
3       BU00340202  2014        0.804254  0.008009  0.000108  0.002760   
4       BU00340203  2014        0.841489  0.008380  0.000113  0.002888   
...            ...   ...             ...       ...       ...       ...   
158626  BU03850501  2024        4.201822  0.049426  0.000198  0.010209   
158627  BU03850601  2024        4.222569  0.047953  0.000208  0.010960   
158628  BU03850701  2024        4.237039  0.046513  0.000226  0.012972   
158629  BU03850801  2024        4.260880  0.051609  0.000193  0.010553   
158630  BU03850901  2024        4.236271  0.047392  0.000210  0.011570   

           PM2_5      PM10  GELUIDSHINDERTOTAAL  AFSTANDTOTHUISARTSENPRAKTIJK  \
0       0.000978  0.001712             0.031359                      0.044207   
1       0.007009  0.012260             0.224557                      0.304468   
2       0.002325  0.004075             0.075240                      0.200975   
3       0.001899  0.003328             0.061453                      0.164147   
4       0.001987  0.003482             0.064298                      0.171747   
...          ...       ...                  ...                           ...   
158626  0.007214  0.014421             0.289616                      2.700000   
158627  0.007407  0.014747             0.298985                      1.000000   
158628  0.007664  0.015213             0.322557                      3.100000   
158629  0.007102  0.014302             0.297161                      3.600000   
158630  0.007531  0.015004             0.294382                      4.000000   

        ...  OPPERVLAKTETOTAAL  OPPERVLAKTELAND  OPPERVLAKTEWATER  \
0       ...           5.420111         5.305270          0.012973   
1       ...          38.828970        38.065935          0.002666   
2       ...          13.063355        12.309700          0.753655   
3       ...          10.669577        10.054024          0.615553   
4       ...          11.163551        10.519500          0.644051   
...     ...                ...              ...               ...   
158626  ...        1082.000000      1026.000000         56.000000   
158627  ...         827.000000       763.000000         64.000000   
158628  ...         570.999999       528.999999         41.000000   
158629  ...         265.999999       254.999999         11.000000   
158630  ...         192.999999       181.999999         11.000000   

        MEESTVOORKOMENDEPOSTCODE  DEKKINGSPERCENTAGE  MATEVANSTEDELIJKHEID  \
0                     143.694917            0.637151              0.212384   
1                    1029.501582            4.562752              1.522339   
2                     340.903332            1.507310              0.502437   
3                     278.434923            1.231105              0.410368   
4                     291.325742            1.288102              0.429367   
...                          ...                 ...                   ...   
158626               1473.000000            1.000000              5.000000   
158627               1472.000000            1.000000              5.000000   
158628               1470.999996            1.000000              5.000000   
158629               1475.999996            1.000000              5.000000   
158630               1476.999989            1.000000              5.000000   

        OMGEVINGSADRESSENDICHTHEID  VLIEGTUIG     TREIN  \
0                       176.241511   0.264182  0.094708   
1                      1255.366587   1.902524  0.684759   
2                       474.049070   0.552680  0.175853   
3                       387.182535   0.451405  0.143629   
4                       405.108088   0.472304  0.150279   
...                        

## Cleaning remaining NaNs

In [7]:
all_features.replace(to_replace=-999, value=None)

BUURTCODE  YEAR LEEFBAAROMETER     GROEN        EC       NO2  \
0       BU00340101  2014       0.422447  0.002708  0.000055  0.001401   
1       BU00340102  2014       3.028834  0.018978  0.000391  0.010034   
2       BU00340201  2014       0.984693  0.009806  0.000132   0.00338   
3       BU00340202  2014       0.804254  0.008009  0.000108   0.00276   
4       BU00340203  2014       0.841489   0.00838  0.000113  0.002888   
...            ...   ...            ...       ...       ...       ...   
158626  BU03850501  2024       4.201822  0.049426  0.000198  0.010209   
158627  BU03850601  2024       4.222569  0.047953  0.000208   0.01096   
158628  BU03850701  2024       4.237039  0.046513  0.000226  0.012972   
158629  BU03850801  2024        4.26088  0.051609  0.000193  0.010553   
158630  BU03850901  2024       4.236271  0.047392   0.00021   0.01157   

           PM2_5      PM10 GELUIDSHINDERTOTAAL AFSTANDTOTHUISARTSENPRAKTIJK  \
0       0.000978  0.001712            0.031359                     0.044207   
1       0.007009   0.01226            0.224557                     0.304468   
2       0.002325  0.004075             0.07524                     0.200975   
3       0.001899  0.003328            0.061453                     0.164147   
4       0.001987  0.003482            0.064298                     0.171747   
...          ...       ...                 ...                          ...   
158626  0.007214  0.014421            0.289616                          2.7   
158627  0.007407  0.014747            0.298985                          1.0   
158628  0.007664  0.015213            0.322557                          3.1   
158629  0.007102  0.014302            0.297161                          3.6   
158630  0.007531  0.015004            0.294382                          4.0   

        ... OPPERVLAKTETOTAAL OPPERVLAKTELAND OPPERVLAKTEWATER  \
0       ...          5.420111         5.30527         0.012973   
1       ...          38.82897       38.065935         0.002666   
2       ...         13.063355         12.3097         0.753655   
3       ...         10.669577       10.054024         0.615553   
4       ...         11.163551         10.5195         0.644051   
...     ...               ...             ...              ...   
158626  ...            1082.0          1026.0             56.0   
158627  ...             827.0           763.0             64.0   
158628  ...        570.999999      528.999999             41.0   
158629  ...        265.999999      254.999999             11.0   
158630  ...        192.999999      181.999999             11.0   

       MEESTVOORKOMENDEPOSTCODE DEKKINGSPERCENTAGE MATEVANSTEDELIJKHEID  \
0                    143.694917           0.637151             0.212384   
1                   1029.501582           4.562752             1.522339   
2                    340.903332            1.50731             0.502437   
3                    278.434923           1.231105             0.410368   
4                    291.325742           1.288102             0.429367   
...                         ...                ...                  ...   
158626                   1473.0                1.0                  5.0   
158627                   1472.0                1.0                  5.0   
158628              1470.999996                1.0                  5.0   
158629              1475.999996                1.0                  5.0   
158630              1476.999989                1.0                  5.0   

       OMGEVINGSADRESSENDICHTHEID VLIEGTUIG     TREIN GELUIDSHINDERINDUSTRIE  
0                      176.241511  0.264182  0.094708               0.223003  
1                     1255.366587  1.902524  0.684759               1.597896  
2                       474.04907   0.55268  0.175853               0.527559  
3                      387.182535  0.451405  0.143629               0.430887  
4                      405.108088  0.472304  0.150279               0.450836  
...            

In [8]:
feature_cols = all_features.drop(["BUURTCODE","YEAR"],axis=1).columns.values

In [25]:
all_features.isnull().sum()

BUURTCODE                        0
YEAR                             0
LEEFBAAROMETER                4160
GROEN                           28
EC                              49
                              ... 
MATEVANSTEDELIJKHEID             0
OMGEVINGSADRESSENDICHTHEID       0
VLIEGTUIG                     7548
TREIN                         7801
GELUIDSHINDERINDUSTRIE        9323
Length: 218, dtype: int64

In [29]:
all_features

BUURTCODE  YEAR  LEEFBAAROMETER     GROEN        EC       NO2  \
0       BU00340101  2014        0.422447  0.002708  0.000055  0.001401   
1       BU00340102  2014        3.028834  0.018978  0.000391  0.010034   
2       BU00340201  2014        0.984693  0.009806  0.000132  0.003380   
3       BU00340202  2014        0.804254  0.008009  0.000108  0.002760   
4       BU00340203  2014        0.841489  0.008380  0.000113  0.002888   
...            ...   ...             ...       ...       ...       ...   
158626  BU03850501  2024        4.201822  0.049426  0.000198  0.010209   
158627  BU03850601  2024        4.222569  0.047953  0.000208  0.010960   
158628  BU03850701  2024        4.237039  0.046513  0.000226  0.012972   
158629  BU03850801  2024        4.260880  0.051609  0.000193  0.010553   
158630  BU03850901  2024        4.236271  0.047392  0.000210  0.011570   

           PM2_5      PM10  GELUIDSHINDERTOTAAL  AFSTANDTOTHUISARTSENPRAKTIJK  \
0       0.000978  0.001712             0.031359                      0.044207   
1       0.007009  0.012260             0.224557                      0.304468   
2       0.002325  0.004075             0.075240                      0.200975   
3       0.001899  0.003328             0.061453                      0.164147   
4       0.001987  0.003482             0.064298                      0.171747   
...          ...       ...                  ...                           ...   
158626  0.007214  0.014421             0.289616                      2.700000   
158627  0.007407  0.014747             0.298985                      1.000000   
158628  0.007664  0.015213             0.322557                      3.100000   
158629  0.007102  0.014302             0.297161                      3.600000   
158630  0.007531  0.015004             0.294382                      4.000000   

        ...  OPPERVLAKTETOTAAL  OPPERVLAKTELAND  OPPERVLAKTEWATER  \
0       ...           5.420111         5.305270          0.012973   
1       ...          38.828970        38.065935          0.002666   
2       ...          13.063355        12.309700          0.753655   
3       ...          10.669577        10.054024          0.615553   
4       ...          11.163551        10.519500          0.644051   
...     ...                ...              ...               ...   
158626  ...        1082.000000      1026.000000         56.000000   
158627  ...         827.000000       763.000000         64.000000   
158628  ...         570.999999       528.999999         41.000000   
158629  ...         265.999999       254.999999         11.000000   
158630  ...         192.999999       181.999999         11.000000   

        MEESTVOORKOMENDEPOSTCODE  DEKKINGSPERCENTAGE  MATEVANSTEDELIJKHEID  \
0                     143.694917            0.637151              0.212384   
1                    1029.501582            4.562752              1.522339   
2                     340.903332            1.507310              0.502437   
3                     278.434923            1.231105              0.410368   
4                     291.325742            1.288102              0.429367   
...                          ...                 ...                   ...   
158626               1473.000000            1.000000              5.000000   
158627               1472.000000            1.000000              5.000000   
158628               1470.999996            1.000000              5.000000   
158629               1475.999996            1.000000              5.000000   
158630               1476.999989            1.000000              5.000000   

        OMGEVINGSADRESSENDICHTHEID  VLIEGTUIG     TREIN  \
0                       176.241511   0.264182  0.094708   
1                      1255.366587   1.902524  0.684759   
2                       474.049070   0.552680  0.175853   
3                       387.182535   0.451405  0.143629   
4                       405.108088   0.472304  0.150279   
...                        

In [30]:
all_features = all_features.groupby('BUURTCODE').apply(lambda group: group.interpolate(method='linear')).reset_index(drop=True)

C:\Users\AratrikaD\AppData\Local\Temp\ipykernel_16020\4130314164.py:1: FutureWarning: DataFrame.interpolate with object dtype is deprecated and will raise in a future version. Call obj.infer_objects(copy=False) before interpolating instead.
  all_features = all_features.groupby('BUURTCODE').apply(lambda group: group.interpolate(method='linear')).reset_index(drop=True)
C:\Users\AratrikaD\AppData\Local\Temp\ipykernel_16020\4130314164.py:1: FutureWarning: DataFrame.interpolate with object dtype is deprecated and will raise in a future version. Call obj.infer_objects(copy=False) before interpolating instead.
  all_features = all_features.groupby('BUURTCODE').apply(lambda group: group.interpolate(method='linear')).reset_index(drop=True)
C:\Users\AratrikaD\AppData\Local\Temp\ipykernel_16020\4130314164.py:1: FutureWarning: DataFrame.interpolate with object dtype is deprecated and will raise in a future version. Call obj.infer_objects(copy=False) before interpolating instead.
  all_features = 

In [32]:
count =all_features.isnull().sum()

In [36]:
drop_vals = count[count>4000].index.values

In [37]:
all_features.drop(inplace=True, labels=drop_vals, axis=1)

In [40]:
count =all_features.isnull().sum()
count[count>0]

LEEFBAAROMETER                   2471
GROEN                              10
EC                                 10
NO2                                10
PM2_5                              10
PM10                               10
GELUIDSHINDERTOTAAL                10
BANENTOTAALBINNEN10KM             246
BANENTOTAALBINNEN20KM             246
BANENTOTAALBINNEN50KM             246
BANENAGRARISCHBINNEN10KM          246
BANENAGRARISCHBINNEN20KM          246
BANENAGRARISCHBINNEN50KM          246
BANENNIJVENERGIEBINNEN10KM        246
BANENNIJVENERGIEBINNEN20KM        246
BANENNIJVENERGIEBINNEN50KM        246
BANENCOMMDIENSTBINNEN10KM         246
BANENCOMMDIENSTBINNEN20KM         246
BANENCOMMDIENSTBINNEN50KM         246
BANENNIETCOMMDIENSTBINNEN10KM     246
BANENNIETCOMMDIENSTBINNEN20KM     246
BANENNIETCOMMDIENSTBINNEN50KM     246
PERSONENAUTOSPERHUISHOUDEN         11
PERSONENAUTOSNAAROPPERVLAKTE       11
dtype: int64

In [41]:
all_features = all_features.groupby('YEAR').apply(lambda group: group.interpolate(method='linear')).reset_index(drop=True)

C:\Users\AratrikaD\AppData\Local\Temp\ipykernel_16020\2355336771.py:1: FutureWarning: DataFrame.interpolate with object dtype is deprecated and will raise in a future version. Call obj.infer_objects(copy=False) before interpolating instead.
  all_features = all_features.groupby('YEAR').apply(lambda group: group.interpolate(method='linear')).reset_index(drop=True)
C:\Users\AratrikaD\AppData\Local\Temp\ipykernel_16020\2355336771.py:1: FutureWarning: DataFrame.interpolate with object dtype is deprecated and will raise in a future version. Call obj.infer_objects(copy=False) before interpolating instead.
  all_features = all_features.groupby('YEAR').apply(lambda group: group.interpolate(method='linear')).reset_index(drop=True)
C:\Users\AratrikaD\AppData\Local\Temp\ipykernel_16020\2355336771.py:1: FutureWarning: DataFrame.interpolate with object dtype is deprecated and will raise in a future version. Call obj.infer_objects(copy=False) before interpolating instead.
  all_features = all_featur

In [42]:
count =all_features.isnull().sum()
count[count>0]

Series([], dtype: int64)

In [43]:
all_features

BUURTCODE  YEAR  LEEFBAAROMETER     GROEN        EC       NO2  \
0       BU00140000  2014        3.995231  0.006693  0.000461  0.016060   
1       BU00140001  2014        4.007582  0.008081  0.000455  0.016122   
2       BU00140002  2014        3.641874  0.006982  0.000415  0.014185   
3       BU00140003  2014        0.753490  0.003809  0.000085  0.003003   
4       BU00140004  2014        0.894338  0.005688  0.000090  0.002953   
...            ...   ...             ...       ...       ...       ...   
158626  BU19923200  2024        4.042706  0.040761  0.000251  0.017493   
158627  BU19923201  2024        4.061659  0.047161  0.000250  0.017436   
158628  BU19923202  2024        4.269247  0.046067  0.000249  0.017399   
158629  BU19923209  2024        4.166958  0.032288  0.000240  0.017008   
158630  BU19923300  2024        4.110712  0.056326  0.000243  0.017815   

           PM2_5      PM10  GELUIDSHINDERTOTAAL  AFSTANDTOTHUISARTSENPRAKTIJK  \
0       0.007822  0.014309             0.298703                      0.284183   
1       0.007893  0.014397             0.283425                      0.190341   
2       0.007163  0.013116             0.288608                      0.260024   
3       0.001451  0.002648             0.059165                      0.085903   
4       0.001722  0.003162             0.068266                      0.146036   
...          ...       ...                  ...                           ...   
158626  0.007697  0.015455             0.327098                      3.400000   
158627  0.007677  0.015409             0.321582                      3.600000   
158628  0.007667  0.015397             0.330565                      3.800000   
158629  0.007543  0.015186             0.315714                      3.592785   
158630  0.007529  0.015110             0.345281                      4.900000   

        ...  MOTORFIETSEN  AFSTANDTOTSCHOOL  SCHOLENBINNEN3KM  \
0       ...     49.888193          0.375635         14.757827   
1       ...    166.508675          0.666068         17.033365   
2       ...     69.329417          0.691056         13.847204   
3       ...      6.063573          0.121271          2.891182   
4       ...     12.225972          0.108682          3.353267   
...     ...           ...               ...               ...   
158626  ...     30.000000          0.400000          1.500000   
158627  ...     60.000000          0.800000          1.000000   
158628  ...     10.000000          0.500000          1.000000   
158629  ...     25.000000          2.195591          1.197595   
158630  ...      0.000000          4.300000          0.000000   

        OPPERVLAKTETOTAAL  OPPERVLAKTELAND  OPPERVLAKTEWATER  \
0               18.490892        17.547828          0.943063   
1               58.045759        52.336699          5.709061   
2               20.233320        18.501707          1.725773   
3                8.553599         8.039100          0.514499   
4               14.388711        13.969846          0.418865   
...                   ...              ...               ...   
158626          21.000000        20.000000          0.000000   
158627          30.000000        27.000000          4.000000   
158628          17.000000        11.000000          6.000000   
158629         884.000000       809.000000         75.000000   
158630         233.000000       121.000000        112.000000   

        MEESTVOORKOMENDEPOSTCODE  DEKKINGSPERCENTAGE  MATEVANSTEDELIJKHEID  \
0                    9154.228572            0.942569              0.942569   
1                    9241.205004            0.951622              0.951622   
2                    8415.392590            0.866582              0.866582   
3                    1696.287864            0.174554              0.174554   
4                    2090.053623            0.215098              0.215098   
...                          ...                 ...                   ...   
158626               3238.000000            1.00000

In [44]:
all_features.to_csv("../../housing-data/all_neighborhood_features.csv", index=False)

## Extract table for buurten in rijnmond

In [1]:
import pandas as pd
all_features = pd.read_csv("../../housing-data/all_neighborhood_features.csv")
rott_adj = pd.read_csv("../../housing-data/rotterdam_adj_2023.csv")

In [2]:
rott_features = all_features[all_features["BUURTCODE"].isin(rott_adj.columns.values)]
rott_features

BUURTCODE  YEAR  LEEFBAAROMETER     GROEN        EC       NO2  \
5960    BU04890101  2014        4.085167  0.019481  0.000689  0.021756   
5961    BU04890102  2014        4.034464  0.041062  0.000660  0.020684   
5962    BU04890103  2014        4.110514  0.031598  0.000684  0.022700   
5963    BU04890204  2014        4.110993  0.037557  0.000684  0.022711   
5964    BU04890205  2014        4.048586  0.038952  0.000666  0.021961   
...            ...   ...             ...       ...       ...       ...   
158626  BU19923200  2024        4.042706  0.040761  0.000251  0.017493   
158627  BU19923201  2024        4.061659  0.047161  0.000250  0.017436   
158628  BU19923202  2024        4.269247  0.046067  0.000249  0.017399   
158629  BU19923209  2024        4.166958  0.032288  0.000240  0.017008   
158630  BU19923300  2024        4.110712  0.056326  0.000243  0.017815   

           PM2_5      PM10  GELUIDSHINDERTOTAAL  AFSTANDTOTHUISARTSENPRAKTIJK  \
5960    0.010006  0.017313             0.323869                      0.400000   
5961    0.009676  0.016755             0.304635                      0.293726   
5962    0.009859  0.017139             0.322656                      0.200000   
5963    0.009891  0.017191             0.325598                      0.400000   
5964    0.009820  0.017036             0.301614                      0.500000   
...          ...       ...                  ...                           ...   
158626  0.007697  0.015455             0.327098                      3.400000   
158627  0.007677  0.015409             0.321582                      3.600000   
158628  0.007667  0.015397             0.330565                      3.800000   
158629  0.007543  0.015186             0.315714                      3.592785   
158630  0.007529  0.015110             0.345281                      4.900000   

        ...  MOTORFIETSEN  AFSTANDTOTSCHOOL  SCHOLENBINNEN3KM  \
5960    ...      9.999997          0.800000          9.099997   
5961    ...      9.796313          0.293398          8.797291   
5962    ...     29.999992          0.300000         12.199997   
5963    ...      9.999997          0.700000         11.199997   
5964    ...     19.999993          0.900000          9.099997   
...     ...           ...               ...               ...   
158626  ...     30.000000          0.400000          1.500000   
158627  ...     60.000000          0.800000          1.000000   
158628  ...     10.000000          0.500000          1.000000   
158629  ...     25.000000          2.195591          1.197595   
158630  ...      0.000000          4.300000          0.000000   

        OPPERVLAKTETOTAAL  OPPERVLAKTELAND  OPPERVLAKTEWATER  \
5960            12.999996        12.999996               0.0   
5961            17.599499        17.599499               0.0   
5962            13.999996        13.999996               0.0   
5963            51.999987        51.999987               0.0   
5964             6.999998         6.999998               0.0   
...                   ...              ...               ...   
158626          21.000000        20.000000               0.0   
158627          30.000000        27.000000               4.0   
158628          17.000000        11.000000               6.0   
158629         884.000000       809.000000              75.0   
158630         233.000000       121.000000             112.0   

        MEESTVOORKOMENDEPOSTCODE  DEKKINGSPERCENTAGE  MATEVANSTEDELIJKHEID  \
5960                 2990.999057            1.000000              1.999999   
5961                 2923.542404            0.977446              1.954893   
5962                 2991.999193            1.000000              1.999999   
5963                 2990.999252            1.000000              1.999999   
5964                 2990.999025            1.000000              1.999999   
...                          ...                 ...                   ...   
158626               3238.000000            1.00000

In [3]:
rott_features.to_csv("../../housing-data/all_neighborhood_features_rotterdam.csv", index=False)